#### Clustering asthma-related papers, among publications referring to different kind of coronaviruses

In [107]:
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import PCA
from sklearn import preprocessing
import matplotlib.pyplot as plt
import pandas as pd

In [108]:
import nltk
import string
from nltk.stem import PorterStemmer
from sklearn.cluster import KMeans
from langdetect import detect

In [109]:
import plotly.express as px

In [110]:
from nltk.corpus import stopwords
sw = stopwords.words("english")

Only those papers where the word "asthma" appears at least once in their abstract were selected. The papers were downloaded in order to be more easily handled, locally. 

In [111]:
asthma_df = pd.read_csv("asthma_data.csv")
asthma_df.head()

cord_uid                                       sha source_x  \
0  qva0jt86  4ba79e54ecf81b30b56461a6aec2094eaf7b7f06      PMC   
1  chz8luni  d68d71553d3a31381c0c3851351f912a9a7be1c9      PMC   
2  3zh8jmc2  fe2000f280297c40bc53ce95d703a9ca6aac19fd      PMC   
3  7p3b6tyf  3ccbd07ee1865e4f2afffdb6cc8b6039ab605ee7      PMC   
4  xrsyj1tc  fa88fbb8716e5fca7d513bcb5a0a608456a59205      PMC   

                                               title  \
0  Relevance of human metapneumovirus in exacerba...   
1  Surfactant therapy for acute respiratory failu...   
2  Differential Regulation of Type I Interferon a...   
3  The Tennessee Children's Respiratory Initiativ...   
4  Analysing the eosinophil cationic protein - a ...   

                                doi       pmcid   pubmed_id license  \
0           10.1186/1465-9921-6-150  PMC1334186  16371156.0   cc-by   
1                    10.1186/cc5944  PMC2206432  17573963.0   cc-by   
2      10.1371/journal.ppat.1000587  PMC2736567  19806178.0   cc-by   
3  10.1111/j.1440-1843.2010.01743.x  PMC2992986  20409023.0   no-cc   
4           10.1186/1465-9921-12-10  PMC3030543  21235798.0   cc-by   

                                            abstract publish_time  ...  \
0  BACKGROUND AND METHODS: Human metapneumovirus ...   2005-12-21  ...   
1  INTRODUCTION: Exogenous surfactant is used to ...   2007-06-15  ...   
2  A number of paramyxoviruses are responsible fo...   2009-09-18  ...   
3  Background and objective: The ‘attack rate’ of...   2010-04-08  ...   
4  Eosinophil granulocytes reside in respiratory ...   2011-01-14  ...   

       journal mag_id  who_covidence_id arxiv_id  \
0   Respir Res    NaN               NaN      NaN   
1    Crit Care    NaN               NaN      NaN   
2  PLoS Pathog    NaN               NaN      NaN   
3  Respirology    NaN               NaN      NaN   
4   Respir Res    NaN               NaN      NaN   

                                      pdf_json_files  \
0  document_parses/pdf_json/4ba79e54ecf81b30b5646...   
1  document_parses/pdf_json/d68d71553d3a31381c0c3...   
2  document_parses/pdf_json/fe2000f280297c40bc53c...   
3  document_parses/pdf_json/3ccbd07ee1865e4f2afff...   
4  document_parses/pdf_json/fa88fbb8716e5fca7d513...   

                                 pmc_json_files  \
0  document_parses/pmc_json/PMC1334186.xml.json   
1  document_parses/pmc_json/PMC2206432.xml.json   
2  document_parses/pmc_json/PMC2736567.xml.json   
3  document_parses/pmc_json/PMC2992986.xml.json   
4  document_parses/pmc_json/PMC3030543.xml.json   

                                                 url s2_id  \
0  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC1...   NaN   
1  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC2...   NaN   
2  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC2...   NaN   
3  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC2...   NaN   
4  https://www.ncbi.nlm.nih.gov/pmc/articles/PMC3...   NaN   

                                      abstract_lower  \
0  background and methods: human metapneumovirus ...   
1  introduction: exogenous surfactant is used to ...   
2  a number of paramyxoviruses are responsible fo...   
3  background and objective: the ‘attack rate’ of...   
4  eosinophil granulocytes reside in respiratory ...   

                                         title_lower  
0  relevance of human metapneumovirus in exacerba...  
1  surfactant therapy for acute respiratory failu...  
2  differential regulation of type i interferon a...  
3  the tennessee children's respiratory initiativ...  
4  analysing the eosinophil cationic protein - a ...  

[5 rows x 21 columns]

There are 2567 papers containing the word "asthma", among the coronavirus-related publications 

In [112]:
asthma_df.shape

(2567, 21)

Between these publication docs, there are papers written in rnglish, french, german language and perhaps some more. For this project we keep in our analysis only papers in eglish. Like that, we avoid having, later on, clusters of papers only of the same langugae but which have not nevessarily similar context.

To do so, we use the *langdetect* google library to dect the language of the "abstract" column in our datsframe. We create a new dataframe column which indicates the language of the abstract. So we have "en" for english, "fr" for french etc. Papers that are non-english are then excluded from the dataframe.

In [113]:
asthma_df["lang_detect"] = asthma_df["abstract"].apply(detect)

In [114]:
asthma_df["lang_detect"].value_counts()

en    2528
de      12
fr      11
es       8
ru       3
pt       3
nl       2
Name: lang_detect, dtype: int64

We now have 2528 papers in total, written in english.

In [115]:
asthma_df = asthma_df.loc[asthma_df['lang_detect'] == "en"]
asthma_df.shape

(2528, 22)

We divide the papers between those published before the new coronavirus SARS-CoV-2 has appeared (December 2019) and those published after the COVID-19 outbreak. We pick December 2019 as the cut-off date.

In [116]:
asthma_before_covid = asthma_df.loc[asthma_df['publish_time']<"2019-12-01"].reset_index(drop=True)
asthma_after_covid = asthma_df.loc[asthma_df['publish_time']>="2019-12-01"].reset_index(drop=True)

Below, for both these two groups of papers, we follow the same data processing. The steps followed are:

* Tokenization of the papers' abstracts text
* Stemming of the tokens 
* Use of the TfidfVectorizer 

#### Papers before COVID-19

In [117]:
texts_before = asthma_before_covid["abstract_lower"].tolist()

In [118]:
def custom_tokenizer(str_input):
    
    stemmer = PorterStemmer()
    words = nltk.word_tokenize(str_input)
    words = [word for word in words if word.lower() not in sw]
    print(words)

    words = [word.replace('â¡', '') for word in words]
    words = [word.replace('â¢', '') for word in words]
    words = [word.replace('â£', '') for word in words]
    
    words = [''.join(c for c in word if c not in string.punctuation+'©±×≤≥●＜--“”→„') for word in words]
    words = [word for word in words if word not in ['‘', '’', '„']]
        
    words = [word for word in words if word]
    words = [word for word in words if not any(char.isdigit() for char in word)]
    
    #remove stop words before stemming - nltk list of stop words - read file and tolist
    words = [stemmer.stem(word) for word in words]
    return words

In [119]:
string_test = "Wilson Tour 110 we Tennis Racket The Wilson Tour 110 Tennis myself Racket is a fantastic choice for any new starter to the sport, with its lightweight frame it allows easy swing. Its gripped handle promotes a comfortable feel and assists in controlling shots."

In [120]:
custom_tokenizer(string_test)

['Wilson', 'Tour', '110', 'Tennis', 'Racket', 'Wilson', 'Tour', '110', 'Tennis', 'Racket', 'fantastic', 'choice', 'new', 'starter', 'sport', ',', 'lightweight', 'frame', 'allows', 'easy', 'swing', '.', 'gripped', 'handle', 'promotes', 'comfortable', 'feel', 'assists', 'controlling', 'shots', '.']


['wilson',
 'tour',
 'tenni',
 'racket',
 'wilson',
 'tour',
 'tenni',
 'racket',
 'fantast',
 'choic',
 'new',
 'starter',
 'sport',
 'lightweight',
 'frame',
 'allow',
 'easi',
 'swing',
 'grip',
 'handl',
 'promot',
 'comfort',
 'feel',
 'assist',
 'control',
 'shot']

In [121]:
vec_before = TfidfVectorizer(min_df=5,tokenizer=custom_tokenizer,
                             max_features=2000,
                      stop_words='english')
matrix_before = vec_before.fit_transform(texts_before)
df_before = pd.DataFrame(matrix_before.toarray(), columns=vec_before.get_feature_names())
df_before.head()

[]
[]
['thence']
['becoming']
[]
['much']
['front']
['less']
['anything']
[]
[]
[]
['upon']
['behind']
['five']
[]
['somewhere']
[]
[]
[]
['two']
[]
[]
['therefore']
['made']
[]
['always']
['part']
['everything']
['anyhow']
[]
['every']
['onto']
[]
['together']
[]
['last']
['else']
['never']
[]
[]
['already']
[]
['inc']
[]
['thereafter']
['whither']
[]
[]
['anyone']
['since']
['everywhere']
['everyone']
[]
[]
['three']
['found']
['first']
['etc']
['enough']
[]
[]
['moreover']
[]
[]
['often']
[]
[]
['elsewhere']
[]
['sometimes']
['hence']
['anyway']
['nine']
['call']
['whatever']
['hasnt']
[]
['bottom']
[]
['ever']
[]
['around']
[]
[]
['would']
['mostly']
[]
[]
['becomes']
['whereupon']
['whence']
['twenty']
['sometime']
[]
['namely']
['either']
[]
[]
['beside']
[]
[]
[]
[]
['seemed']
['someone']
['top']
['ltd']
[]
['third']
['besides']
['beforehand']
['herein']
[]
['perhaps']
['whenever']
[]
['sincere']
[]
['describe']
['beyond']
['eg']
[]
['seems']
['none']
['un']
['please']
['rather'

c:\users\katerina\appdata\local\programs\python\python37\lib\site-packages\sklearn\feature_extraction\text.py:386: UserWarning:

Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth', 'twelv', 'twenti', 'whatev', 'whenc', 'whenev', 'wherea', 'whereaft', 'wherebi', 'wherev'] not in stop_words.



['background', ':', 'first', 'case', '2009', 'pandemic', 'influenza', '(', 'h1n1', ')', 'virus', 'infection', 'documented', 'hospital', '10th', 'august', '2009.', 'metdods', 'findings', ':', 'real-time', 'reverse-transcriptase-polymerase-chain-reaction', '(', 'rt-pcr', ')', 'testing', 'used', 'confirm', 'diagnosis', '.', 'patients', 'treated', 'oseltamivir', 'first', 'day', 'hospitalization', '.', 'upon', 'admission', '12/44', 'local', 'patchy', 'shadowing', 'chest', 'x-ray', 'additionally', 'antibiotic', 'regimen', 'added', 'patients', 'pneumonia', 'suspected', 'based', 'clinical', 'evidence', '.', 'total', '44', 'patients', 'hospitalized', '15/44', 'asthma', ',', '6/44', 'copd', ',', '5/44', 'leukemia', '.', 'lung', 'function', 'evaluated', 'forced', 'vital', 'capacity', ',', 'forced', 'expiratory', 'volume', '1', 'sec', 'diffused', 'carbon', 'monoxide', 'upon', 'discharge', 'every', '3', 'months', ',', '6', 'months', 'observation', 'completed', 'discharge', '.', 'purpose', 'retrospe

['dilated', 'cardiomyopathy', 'disease', 'left', 'ventricular', 'dysfunction', 'accompanied', 'impairment', 'β', '(', '1', ')', '-adrenergic', 'receptor', '(', 'β', '(', '1', ')', '-ar', ')', 'signal', 'cascade', '.', 'disturbed', 'β', '(', '1', ')', '-ar', 'function', 'may', 'based', 'elevated', 'sympathetic', 'tone', 'observed', 'patients', 'heart', 'failure', '.', 'prolonged', 'adrenergic', 'stimulation', 'may', 'induce', 'metabolic', 'electrophysiological', 'disturbances', 'myocardium', ',', 'resulting', 'tachyarrhythmia', 'leads', 'development', 'heart', 'failure', 'human', 'sudden', 'death', '.', 'hence', ',', 'β', '(', '1', ')', '-ar', 'considered', 'promising', 'drug', 'target', 'attempts', 'develop', 'effective', 'specific', 'drug', 'tempting', 'pharmaceutical', 'target', 'slowed', 'due', 'lack', '3d', 'structure', 'homo', 'sapiens', 'β', '(', '1', ')', '-ar', '(', 'hsβadr1', ')', '.', 'study', 'encompasses', 'elucidation', '3d', 'structural', 'physicochemical', 'properties', 

['background', ':', 'plants', 'used', 'treatment', 'cancer', 'one', 'attracted', 'scientific', 'interest', ',', 'euphorbia', 'tirucalli', '(', 'e.', 'tirucalli', ')', ',', 'used', 'treatment', 'asthma', ',', 'ulcers', ',', 'warts', 'active', 'components', 'activities', 'scientifically', 'proven', 'antimutagenic', ',', 'anti-inflammatory', 'anticancer', '.', 'methods', ':', 'evaluate', 'influence', 'antitumoral', 'fraction', 'e.', 'tirucalli', 'latex', 'larynx', 'squamous', 'cell', 'carcinoma', '(', 'hep-2', ')', ',', 'morphology', ',', 'cell', 'proliferation', 'gene', 'expression', '.', 'hep-2', 'cells', 'cultivated', 'complete', 'medium', '(', 'mem', '10', '%', ')', 'treated', 'e.', 'tirucalli', 'latex', '1', ',', '3', ',', '5', '7', 'days', '.', 'statistically', 'analyzing', 'proliferation', 'tested', 'cells', ',', 'cells', 'cultivated', 'rna', 'extraction', 'rapid', 'subtractive', 'hybridization', '(', 'rash', ')', 'technique', 'used', 'identify', 'genes', 'altered', 'expression', '

...

['background', ':', 'major', 'trigger', 'asthma', 'exacerbations', 'infection', 'respiratory', 'virus', ',', 'commonly', 'rhinovirus', '.', 'type', '2', 'inflammation', 'known', 'associated', 'increased', 'risk', 'exacerbations', 'general', '.', 'whether', 'type', '2', 'inflammation', 'baseline', 'increases', 'risk', 'future', 'virus‐induced', 'exacerbations', 'unknown', '.', 'objective', ':', 'assess', 'whether', 'type', '2', 'inflammation', 'associated', 'increased', 'risk', 'virus‐induced', 'exacerbations', 'asthma', '.', 'methods', ':', 'stable', 'asthmatics', 'spirometry', ',', 'skin', 'prick', 'test', ',', 'measurement', 'feno', 'sputum', 'induced', 'differential', 'cell', 'counts', '.', 'patients', 'followed', '18', 'months', ',', 'assessed', 'research', 'unit', 'symptoms', 'exacerbation', '.', 'nasal', 'swabs', 'collected', 'assessments', 'underwent', 'viral', 'detection', 'pcr', '.', 'results', ':', 'total', '81', 'asthma', 'patients', 'recruited', ',', '22', '(', '27', '%', '

['background', ':', 'wheezing', 'illnesses', 'among', 'young', 'children', 'common', ',', 'risk', 'factor', 'asthma', '.', 'however', ',', 'determinants', 'childhood', 'bronchial', 'reactivity', ',', 'key', 'feature', 'asthma', ',', 'largely', 'unknown', '.', 'aim', 'study', 'determine', 'patient', 'characteristics', 'first', 'severe', 'virus-induced', 'wheezing', 'episode', 'associated', 'pulmonary', 'function', 'pre-school', 'age', '.', 'methods', ':', 'study', 'consisted', '76', 'children', 'presenting', 'first', 'wheezing', 'episode', 'ages', '3', '23', 'months', '.', 'study', 'entry', ',', 'viral', 'etiology', ',', 'rhinovirus', 'genome', 'load', ',', 'atopic', 'clinical', 'characteristics', ',', 'standardized', 'questionnaire', 'analyzed', '.', '4-year', 'follow-up', 'visit', ',', 'impulse', 'oscillometry', 'exercise', 'challenge', 'performed', '.', 'results', ':', 'study', 'entry', ',', 'mean', 'age', 'children', '12', 'months', '(', 'sd', '6.0', ')', ',', '57', '(', '75', '%', 

['background', ':', 'chitinase', '3‐like', '1', 'protein', '(', 'chi3l1', ')', '(', 'ykl‐40', 'humans', 'breast', 'regression', 'protein', '[', 'brp', ']', '‐39', 'mice', ')', 'required', 'optimal', 'allergen', 'sensitization', 'th2', 'inflammation', 'various', 'chronic', 'inflammatory', 'diseases', 'including', 'asthma', '.', 'however', ',', 'role', 'chi3l1', 'airway', 'inflammation', 'induced', 'respiratory', 'viruses', 'investigated', '.', 'aim', 'study', 'investigate', 'relationship', 'chi3l1', 'airway', 'inflammation', 'caused', 'respiratory', 'syncytial', 'virus', '(', 'rsv', ')', 'infection', '.', 'methods', ':', 'measured', 'ykl‐40', 'levels', 'human', 'nasopharyngeal', 'aspirate', '(', 'npa', ')', 'hospitalized', 'children', 'presenting', 'acute', 'respiratory', 'symptoms', '.', 'wild‐type', '(', 'wt', ')', 'brp‐39', 'knockout', '(', 'ko', ')', 'c57bl/6', 'mice', 'inoculated', 'live', 'rsv', '(', 'a2', 'strain', ')', '.', 'bronchoalveolar', 'lavage', 'fluid', 'lung', 'tissue',

['background', ':', 'annual', 'burden', 'disease', 'caused', 'indoor', 'air', 'pollution', ',', 'including', 'polluted', 'outdoor', 'air', 'used', 'ventilate', 'indoor', 'spaces', ',', 'estimated', 'correspond', 'loss', '2', 'million', 'healthy', 'life', 'years', 'european', 'union', '(', 'eu', ')', '.', 'based', 'measurements', 'european', 'environment', 'agency', '(', 'eea', ')', ',', 'approximately', '90', '%', 'eu', 'citizens', 'live', 'areas', 'world', 'health', 'organization', '(', ')', 'guidelines', 'air', 'quality', 'particulate', 'matter', 'sized', '<', '2.5', 'mm', '(', 'pm', '(', '2.5', ')', ')', 'met', '.', 'since', 'sources', 'pollution', 'reside', 'indoor', 'outdoor', 'air', ',', 'selecting', 'appropriate', 'ventilation', 'strategy', 'simple', 'straightforward', 'task', '.', 'methods', ':', 'framework', 'developing', 'european', 'health-based', 'ventilation', 'guidelines', 'created', '2010–2013', 'eu-funded', 'healthvent', 'project', '.', 'part', 'project', ',', 'potentia

aberr  abil  abl  abnorm  absenc  absent  absolut  absorpt  abstract  \
0    0.0   0.0  0.0     0.0     0.0     0.0      0.0      0.0       0.0   
1    0.0   0.0  0.0     0.0     0.0     0.0      0.0      0.0       0.0   
2    0.0   0.0  0.0     0.0     0.0     0.0      0.0      0.0       0.0   
3    0.0   0.0  0.0     0.0     0.0     0.0      0.0      0.0       0.0   
4    0.0   0.0  0.0     0.0     0.0     0.0      0.0      0.0       0.0   

   abund  ...    x  xray      year  yield  young  younger   yr    α    β    –  
0    0.0  ...  0.0   0.0  0.000000    0.0    0.0      0.0  0.0  0.0  0.0  0.0  
1    0.0  ...  0.0   0.0  0.000000    0.0    0.0      0.0  0.0  0.0  0.0  0.0  
2    0.0  ...  0.0   0.0  0.000000    0.0    0.0      0.0  0.0  0.0  0.0  0.0  
3    0.0  ...  0.0   0.0  0.039269    0.0    0.0      0.0  0.0  0.0  0.0  0.0  
4    0.0  ...  0.0   0.0  0.035475    0.0    0.0      0.0  0.0  0.0  0.0  0.0  

[5 rows x 2000 columns]

The Kmeans is explained here:
https://towardsdatascience.com/understanding-k-means-clustering-in-machine-learning-6a6e67336aa1

In [122]:
number_of_clusters=10
km_before = KMeans(n_clusters=number_of_clusters)
km_before.fit(matrix_before)

KMeans(n_clusters=10)

Let's have an over view of our cluster's centers (centroids) anf labels. After that, we get the top terms for every cluster. In other wrods, we see which are the most frequently mentioned words per cluster. Note: since we have used Stemming, we only have the root of the words now.

In [123]:
centroids_before, labels_before = km_before.cluster_centers_, km_before.labels_
print(centroids_before)
print(labels_before)

[[0.         0.00346865 0.         ... 0.         0.         0.        ]
 [0.         0.00182432 0.0016059  ... 0.00272646 0.00297322 0.        ]
 [0.         0.00618786 0.00303816 ... 0.0017635  0.00239231 0.00077186]
 ...
 [0.         0.         0.0006882  ... 0.         0.         0.0049591 ]
 [0.00183604 0.00312969 0.00185302 ... 0.00336395 0.00486896 0.00645302]
 [0.         0.00535447 0.         ... 0.         0.         0.        ]]
[7 6 4 ... 6 6 5]


In [124]:
print("Top terms per cluster:")
order_centroids_before = km_before.cluster_centers_.argsort()[:, ::-1]
terms = vec_before.get_feature_names()
for i in range(number_of_clusters):
    top_ten_words = [terms[ind] for ind in order_centroids_before[i, :20]]
    print("Cluster {}: {}".format(i, ' '.join(top_ten_words)))

Top terms per cluster:
Cluster 0: rsv bronchiol rv children infect respiratori infant viru hmpv detect wheez rhinoviru caus viral hospit develop asthma syncyti vaccin rvc
Cluster 1: p level exacerb patient asthma eosinophil subject asthmat viral infect sputum increas day cold group nasal control airway serum symptom
Cluster 2: exacerb asthma infect viral respiratori virus diseas develop review factor airway associ role caus mechan treatment sever risk current trigger
Cluster 3: airway mice inflamm cell hyperrespons respons inflammatori asthma muscl lung increas smooth remodel eosinophil induc regul infect chang express allerg
Cluster 4: cell infect immun respons express respiratori activ diseas role asthma epitheli macrophag viral human inflammatori type protein host viru rv
Cluster 5: wheez children infant risk asthma recurr year respiratori age ill earli factor viral bronchiol associ infect ci develop p episod
Cluster 6: asthma patient use health children studi medic effect ci risk h

In [125]:
order_centroids_before
#word with index 1049 has highest Tfidf value in the first array

array([[1598,  229, 1604, ..., 1115, 1118,    0],
       [1285, 1018,  651, ..., 1069, 1070,    0],
       [ 651,  149,  913, ..., 1090, 1091,    0],
       ...,
       [ 287, 1567, 1360, ...,  952,  950,    0],
       [ 524, 1464, 1054, ..., 1230,  374,  503],
       [ 833,  836,  287, ..., 1156, 1157,    0]], dtype=int64)

PCA and its implementation in Python is explained here: https://jakevdp.github.io/PythonDataScienceHandbook/05.09-principal-component-analysis.html

In [126]:
T = preprocessing.Normalizer().fit_transform(df_before)
# Dimesionality reduction to 2
pca_model = PCA(n_components=2)
pca_model.fit(T) 
T = pca_model.transform(T) 

# transform the 'centroids of KMean'

centroid_pca = pca_model.transform(centroids)


In [127]:
asthma_before_covid['labels'] = km_before.labels_
asthma_before_covid['pca_1'] = T[:, 0]
asthma_before_covid['pca_2'] = T[:, 1]

In [128]:
asthma_before_covid['labels'] = asthma_before_covid['labels'].astype(str)

In [129]:
fig = px.scatter(asthma_before_covid, 
                 x="pca_1", 
                 y="pca_2", 
                 color="labels",
                 hover_data=['title'])

In [130]:
fig.show()

#### After covid-19

In [131]:
texts_after = asthma_after_covid["abstract_lower"].tolist()

In [132]:
vec_after = TfidfVectorizer(tokenizer=custom_tokenizer,
                      stop_words='english', 
                           max_features=1000)
matrix_after = vec_after.fit_transform(texts_after)
df_after = pd.DataFrame(matrix_after.toarray(), columns=vec_after.get_feature_names())


[]
[]
['thence']
['becoming']
[]
['much']
['front']
['less']
['anything']
[]
[]
[]
['upon']
['behind']
['five']
[]
['somewhere']
[]
[]
[]
['two']
[]
[]
['therefore']
['made']
[]
['always']
['part']
['everything']
['anyhow']
[]
['every']
['onto']
[]
['together']
[]
['last']
['else']
['never']
[]
[]
['already']
[]
['inc']
[]
['thereafter']
['whither']
[]
[]
['anyone']
['since']
['everywhere']
['everyone']
[]
[]
['three']
['found']
['first']
['etc']
['enough']
[]
[]
['moreover']
[]
[]
['often']
[]
[]
['elsewhere']
[]
['sometimes']
['hence']
['anyway']
['nine']
['call']
['whatever']
['hasnt']
[]
['bottom']
[]
['ever']
[]
['around']
[]
[]
['would']
['mostly']
[]
[]
['becomes']
['whereupon']
['whence']
['twenty']
['sometime']
[]
['namely']
['either']
[]
[]
['beside']
[]
[]
[]
[]
['seemed']
['someone']
['top']
['ltd']
[]
['third']
['besides']
['beforehand']
['herein']
[]
['perhaps']
['whenever']
[]
['sincere']
[]
['describe']
['beyond']
['eg']
[]
['seems']
['none']
['un']
['please']
['rather'

c:\users\katerina\appdata\local\programs\python\python37\lib\site-packages\sklearn\feature_extraction\text.py:386: UserWarning:

Your stop_words may be inconsistent with your preprocessing. Tokenizing the stop words generated tokens ['afterward', 'alon', 'alreadi', 'alway', 'anoth', 'anyon', 'anyth', 'anywher', 'becam', 'becom', 'besid', 'cri', 'describ', 'els', 'elsewher', 'empti', 'everi', 'everyon', 'everyth', 'everywher', 'fifti', 'formerli', 'forti', 'henc', 'hereaft', 'herebi', 'howev', 'hundr', 'inde', 'latterli', 'mani', 'meanwhil', 'moreov', 'mostli', 'nobodi', 'noon', 'noth', 'nowher', 'otherwis', 'perhap', 'pleas', 'seriou', 'sever', 'sinc', 'sincer', 'sixti', 'someon', 'someth', 'sometim', 'somewher', 'thenc', 'thereaft', 'therebi', 'therefor', 'thu', 'togeth', 'twelv', 'twenti', 'whatev', 'whenc', 'whenev', 'wherea', 'whereaft', 'wherebi', 'wherev'] not in stop_words.



['purpose', ':', 'hypercapnic', 'respiratory', 'failure', '(', 'hrf', ')', 'frequent', 'cause', 'hospitalization', 'common', 'comorbidity', 'hospitalized', 'patients', '.', 'studies', 'addressing', 'factors', 'might', 'predict', 'poor', 'outcomes', 'patient', 'population', '.', 'purpose', 'current', 'study', 'investigate', 'characteristics', 'outcomes', 'patients', 'hospitalized', 'hrf', '.', 'methods', ':', 'study', 'patients', '≥', '18', 'years', 'admitted', 'hrf', '1-year', 'period', '.', 'patients', 'limited', 'life', 'expectancy', 'related', 'conditions', ',', 'non-respiratory', 'cause', 'hrf', ',', 'excluded', '.', 'results', ':', '202', 'subjects', 'met', 'eligibility', 'criteria', ':', '24', '%', 'diagnosis', 'obstructive', 'sleep', 'apnea', ',', '6', '%', 'obesity', 'hypoventilation', ',', '46', '%', 'chronic', 'obstructive', 'pulmonary', 'disease', ',', '10', '%', 'asthma', '.', 'fifteen', '(', '7', '%', ')', 'died', 'index', 'admission', '.', 'forty-one', 'patients', '(', '2

['sickle', 'cell', 'disease', 'characterized', 'vaso-occlusive', 'hemolysis', 'events', 'may', 'occur', 'variable', 'range', 'clinical', 'presentations', '.', 'patients', 'disease', ',', 'particularly', 'acute', 'chest', 'syndrome', ',', 'suffer', 'acute', 'episodes', 'chest', 'pain', 'caused', 'vaso-occlusive', 'crisis', ',', 'tend', 'repeat', ',', 'especially', 'influence', 'lower', 'respiratory', 'infections', ',', 'dehydration', ',', 'cause', 'hypoxemia', '.', 'children', 'adolescents', 'sickle', 'cell', 'disease', 'must', 'periodically', 'evaluated', 'oximetry', ',', 'lung', 'function', 'tests', ',', 'sleep', 'study', ',', 'echocardiograms', 'detect', 'obstructive', 'restrictive', 'diseases', 'frequently', 'worsens', 'lung', 'condition', '.', 'asthma', 'sleep', 'disorders', 'contribute', 'morbidity', 'must', 'controlled', '.']
['atmospheric', 'pollutants', 'cigarette', 'smoke', 'influence', 'human', 'respiratory', 'system', 'induce', 'airway', 'inflammation', ',', 'injury', ',', '

['objectives', ':', 'study', 'aims', 'explore', 'differential', 'impact', 'pandemic', 'clinical', 'presentations', 'outcomes', 'african', 'americans', '(', 'aas', ')', 'compared', 'white', 'patients', '.', 'background', ':', 'aas', 'worse', 'outcomes', 'compared', 'whites', 'facing', 'heart', 'diseases', ',', 'stroke', ',', 'cancer', ',', 'asthma', ',', 'influenza', 'pneumonia', ',', 'diabetes', ',', 'hiv/aids', '.', 'however', ',', 'current', 'study', 'show', 'impact', 'covid-19', 'pandemic', 'aa', 'communities', '.', 'methods', ':', 'retrospective', 'study', 'included', 'patients', 'laboratory-confirmed', 'covid-19', '2', 'tertiary', 'centers', 'new', 'orleans', ',', 'la', '.', 'clinical', 'laboratory', 'data', 'collected', '.', 'multivariate', 'analyses', 'performed', 'identify', 'risk', 'factors', 'associated', 'adverse', 'events', '.', 'results', ':', 'total', '157', 'patients', 'identified', '.', ',', '134', '(', '77', '%', ')', 'aas', ',', 'whereas', '23.4', '%', 'patients', 'wh

...

['background', ':', 'morbidity', 'mortality', 'covid‐19', 'caused', 'novel', 'coronavirus', 'sars‐cov‐2', 'accelerating', 'worldwide', 'novel', 'clinical', 'presentations', 'covid‐19', 'often', 'reported', '.', 'range', 'human', 'cells', 'tissues', 'targeted', 'sars‐cov‐2', ',', 'potential', 'receptors', 'associated', 'regulating', 'factors', 'still', 'largely', 'unknown', '.', 'aim', 'study', 'analyze', 'expression', 'known', 'potential', 'sars‐cov‐2', 'receptors', 'related', 'molecules', 'extensive', 'collection', 'primary', 'human', 'cells', 'tissues', 'healthy', 'subjects', 'different', 'age', 'patients', 'risk', 'factors', 'known', 'comorbidities', 'covid‐19', '.', 'methods', ':', 'performed', 'rna', 'sequencing', 'explored', 'available', 'rna‐seq', 'databases', 'study', 'gene', 'expression', 'co‐expression', 'ace2', ',', 'cd147', '(', 'bsg', ')', ',', 'cd26', '(', 'dpp4', ')', 'direct', 'indirect', 'molecular', 'partners', 'primary', 'human', 'bronchial', 'epithelial', 'cells', '

['abstract', 'background', '300', 'million', 'people', 'carry', 'diagnosis', 'asthma', 'data', 'suggest', 'higher', 'risk', 'infection', 'adverse', 'outcomes', 'sars-cov-2', '.', 'asthma', 'remarkably', 'heterogenous', 'currently', 'unclear', 'patient', 'intrinsic', 'factors', 'may', 'relate', 'covid-19', '.', 'objective', 'identify', 'characterize', 'subsets', 'asthmatics', 'increased', 'risk', 'sars-cov-2', 'infection', '.', 'methods', 'participants', '2', 'large', 'asthma', 'cohorts', 'stratified', 'using', 'clinically', 'relevant', 'parameters', 'identify', 'factors', 'related', 'ace2', 'expression', 'within', 'bronchial', 'epithelium', '.', 'ace-2', 'correlated', 'gene', 'signatures', 'used', 'interrogate', 'publicly', 'available', 'databases', 'identify', 'upstream', 'signaling', 'events', 'novel', 'therapeutic', 'targets', '.', 'results', 'stratifying', 'type', '2', 'inflammatory', 'biomarkers', ',', 'identified', 'subjects', 'demonstrated', 'low', 'peripheral', 'blood', 'eosino

['introduction', ':', 'coronavirus', 'disease', '(', 'covid-19', ')', 'infection', 'caused', 'novel', 'severe', 'acute', 'respiratory', 'syndrome', 'coronavirus-2', '(', 'sars-cov-2', ')', 'primarily', 'affecting', 'lungs', '.', 'tobacco-related', 'illnesses', 'including', 'asthma', ',', 'chronic', 'obstructive', 'pulmonary', 'disease', '(', 'copd', ')', ',', 'coronary', 'artery', 'disease', 'known', 'reduce', 'lung', 'capacity', 'impair', 'immune', 'system', 'body', 'greatly', 'influence', 'ability', 'fight', 'novel', 'coronavirus', '.', 'purpose', 'state-of-the-art', 'literature', 'review', 'summarize', 'evidence', 'association', 'tobacco', 'use', 'severity', 'covid-19', 'manifestations', '.', 'method', ':', 'articles', 'describing', 'association', 'tobacco', 'use', 'severity', 'covid-19', 'manifestations', 'searched', 'pubmed', ',', 'medline', ',', 'google', '.', 'review', 'covers', 'relevant', 'studies', 'subject', 'published', 'january', '1', ',', '2020', 'september', '10', ',', '

['background', ':', 'severe', 'coronavirus', 'disease', '2019', '(', 'covid-19', ')', 'associated', 'multiple', 'comorbidities', 'characterized', 'auto-aggressive', 'inflammatory', 'state', 'leading', 'massive', 'collateral', 'damage', '.', 'identify', 'preventive', 'therapeutic', 'strategies', 'severe', 'acute', 'respiratory', 'syndrome', 'coronavirus', '2', '(', 'sars-cov-2', ')', ',', 'important', 'ascertain', 'molecular', 'interactions', 'virus', 'host', ',', 'translate', 'disease', 'pathophysiology', '.', 'methods', ':', 'matched', 'virus-human', 'protein', 'interactions', 'human', 'coronaviruses', 'respiratory', 'viruses', 'lists', 'genes', 'associated', 'autoimmune', 'diseases', 'comorbidities', 'associated', 'worse', 'covid-19', 'course', '.', 'selected', 'genes', 'included', 'statistically', 'significant', 'intersection', 'sars-cov-2', 'network', 'disease', 'associated', 'gene', 'sets', ',', 'identifying', 'meta-interactome', '.', 'analyzed', 'meta-interactome', 'genes', 'expr

['background', ':', 'adverse', 'effects', 'covid-19', 'pandemic', 'mental', 'health', 'high-risk', 'group', 'patients', 'morbidity', 'mortality', 'impact', 'public', 'health', 'long', 'term', 'clearly', 'determined', '.', 'objective', ':', 'determine', 'level', 'covid-19', 'related', 'transmission', 'fear', 'anxiety', 'healthcare', 'workers', 'patients', 'primary', 'immunodeficiency', 'disorder', '(', 'pid', ')', ',', 'severe', 'asthma', ',', 'ones', 'comorbidities', '.', 'methods', ':', 'healthcare', 'workers', 'patients', 'pid', ',', 'severe', 'asthma', '(', 'patients', 'receiving', 'biological', 'agent', 'treatment', ')', ',', 'malignancy', ',', 'cardiovascular', 'disease', ',', 'hypertension', '(', '90', '%', 'patients', 'receiving', 'acei', 'arb', 'therapy', ')', ',', 'diabetes', 'mellitus', '(', '42', '%', 'patients', 'receiving', 'dpp-4', 'inhibitor', 'therapy', ')', 'included', 'study', '.', 'total', '560', 'participants', ',', '80', 'individuals', 'group', ',', 'provided', '.'

In [133]:
df_after.head()

abil  abl  abnorm  absenc  abstract  access  accord  account  accumul  \
0   0.0  0.0     0.0     0.0       0.0     0.0     0.0      0.0      0.0   
1   0.0  0.0     0.0     0.0       0.0     0.0     0.0      0.0      0.0   
2   0.0  0.0     0.0     0.0       0.0     0.0     0.0      0.0      0.0   
3   0.0  0.0     0.0     0.0       0.0     0.0     0.0      0.0      0.0   
4   0.0  0.0     0.0     0.0       0.0     0.0     0.0      0.0      0.0   

   achiev  ...  world  worldwid  wors  worsen  wuhan      year  york  young  \
0     0.0  ...    0.0       0.0   0.0     0.0    0.0  0.000000   0.0    0.0   
1     0.0  ...    0.0       0.0   0.0     0.0    0.0  0.000000   0.0    0.0   
2     0.0  ...    0.0       0.0   0.0     0.0    0.0  0.076703   0.0    0.0   
3     0.0  ...    0.0       0.0   0.0     0.0    0.0  0.000000   0.0    0.0   
4     0.0  ...    0.0       0.0   0.0     0.0    0.0  0.000000   0.0    0.0   

    younger  youth  
0  0.300018    0.0  
1  0.000000    0.0  
2  0.000000    0.0  
3  0.000000    0.0  
4  0.000000    0.0  

[5 rows x 1000 columns]

In [134]:
number_of_clusters=10
km_after = KMeans(n_clusters=number_of_clusters)
km_after.fit(matrix_after)
km_after.fit

<bound method KMeans.fit of KMeans(n_clusters=10)>

In [135]:
centroids_after, labels_after = km_after.cluster_centers_, km_after.labels_
print(centroids_after)
print(labels_after)

[[0.00160991 0.00635285 0.00113102 ... 0.00320728 0.00117456 0.00768973]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.00490363 0.         ... 0.         0.         0.        ]
 ...
 [0.00108799 0.         0.         ... 0.00494228 0.00761792 0.        ]
 [0.00640185 0.00318048 0.0020974  ... 0.00032376 0.         0.        ]
 [0.00081114 0.00115028 0.01133194 ... 0.00647969 0.00554488 0.        ]]
[9 1 7 ... 8 7 0]


In [136]:
print("Top terms per cluster:")
order_centroids_after = km_after.cluster_centers_.argsort()[:, ::-1]
terms = vec_after.get_feature_names()
for i in range(number_of_clusters):
    top_ten_words = [terms[ind] for ind in order_centroids_after[i, :20]]
    print("Cluster {}: {}".format(i, ' '.join(top_ten_words)))

Top terms per cluster:
Cluster 0: health care telemedicin patient use asthma provid pandem diseas visit studi measur condit control healthcar group depress individu impact medic
Cluster 1: express cell gene receptor airway asthma epitheli associ sever copd protein diseas infect bronchial patient entri upregul increas level asthmat
Cluster 2: air pollut health lockdown exposur human pm impact particul qualiti environment matter asthma reduc effect respiratori citi econom level diseas
Cluster 3: diseas respiratori patient sever coronaviru infect case acut caus asthma syndrom pandem chronic symptom lung report present risk underli individu
Cluster 4: patient asthma sever corticosteroid inhal recommend treatment use exacerb infect pandem risk control diseas continu manag medic current evid allerg
Cluster 5: children asthma pediatr infect respiratori hospit patient p year age sever diseas studi clinic symptom risk admiss vs adult present
Cluster 6: biolog therapi patient sever asthma treatm

In [137]:
order_centroids_after

array([[386, 123, 911, ..., 652, 362, 709],
       [331, 128, 368, ..., 551, 549,   0],
       [ 36, 661, 386, ..., 568, 569,   0],
       ...,
       [146, 632, 790, ..., 598, 151, 999],
       [511, 274, 128, ..., 757, 911, 999],
       [632, 400, 222, ..., 546, 530, 999]], dtype=int64)

In [138]:
T_after = preprocessing.Normalizer().fit_transform(df_after)
# Dimesionality reduction to 2
pca_model = PCA(n_components=2)
pca_model.fit(T_after) 
T_after = pca_model.transform(T_after) 

centroid_pca_after = pca_model.transform(centroids_after)

In [139]:
asthma_after_covid['labels'] = km_after.labels_
asthma_after_covid['pca_1'] = T_after[:, 0]
asthma_after_covid['pca_2'] = T_after[:, 1]

In [140]:
asthma_after_covid['labels'] = asthma_after_covid['labels'].astype(str)

In [141]:
fig = px.scatter(asthma_after_covid, 
                 x="pca_1", 
                 y="pca_2", 
                 color="labels",
                 hover_data=['title'])

In [142]:
fig.show()